##### Copyright 2020 The TensorFlow Authors.

In [1]:
#@title Licensed under the Apache License, Version 2.0 (the "License");
# you may not use this file except in compliance with the License.
# You may obtain a copy of the License at
#
# https://www.apache.org/licenses/LICENSE-2.0
#
# Unless required by applicable law or agreed to in writing, software
# distributed under the License is distributed on an "AS IS" BASIS,
# WITHOUT WARRANTIES OR CONDITIONS OF ANY KIND, either express or implied.
# See the License for the specific language governing permissions and
# limitations under the License.

<table class="tfo-notebook-buttons" align="left">
  <td><a target="_blank" href="https://www.tensorflow.org/io/tutorials/genome"><img src="https://www.tensorflow.org/images/tf_logo_32px.png">TensorFlow.org에서 보기</a></td>
  <td><a target="_blank" href="https://colab.research.google.com/github/tensorflow/docs-l10n/blob/master/site/ko/io/tutorials/genome.ipynb"><img src="https://www.tensorflow.org/images/colab_logo_32px.png">Google Colab에서 실행하기</a></td>
  <td><a target="_blank" href="https://github.com/tensorflow/docs-l10n/blob/master/site/ko/io/tutorials/genome.ipynb"><img src="https://www.tensorflow.org/images/GitHub-Mark-32px.png">GitHub에서소스 보기</a></td>
      <td><a href="https://storage.googleapis.com/tensorflow_docs/docs-l10n/site/ko/io/tutorials/genome.ipynb"><img src="https://www.tensorflow.org/images/download_logo_32px.png">노트북 다운로드하기</a></td>
</table>

## 개요

이 튜토리얼은 일반적으로 사용되는 게놈 IO 기능을 제공하는 `tfio.genome` 패키지를 시연합니다. 즉, 여러 게놈 파일 형식을 읽고 데이터를 준비하기 위한 몇 가지 일반적인 연산도 제공합니다(예: 원-핫 인코딩 또는 Phred 품질을 확률로 구문 분석).

이 패키지는 [Google Nucleus](https://github.com/google/nucleus) 라이브러리를 사용하여 일부 핵심 기능을 제공합니다. 

## 설정

In [2]:
try:
  %tensorflow_version 2.x
except Exception:
  pass
!pip install -q tensorflow-io

In [3]:
import tensorflow_io as tfio
import tensorflow as tf

## FASTQ 데이터

FASTQ는 기본 품질 정보와 함께 두 가지 시퀀스 정보를 모두 저장하는 일반적인 게놈 파일 형식입니다.

먼저, 샘플 `fastq` 파일을 다운로드하겠습니다.

In [4]:
# Download some sample data:
!curl -OL https://raw.githubusercontent.com/tensorflow/io/master/tests/test_genome/test.fastq

  % Total    % Received % Xferd  Average Speed   Time    Time     Time  Current
                                 Dload  Upload   Total   Spent    Left  Speed
  0     0    0     0    0     0      0      0 --:--:-- --:--:-- --:--:--     0

100   407  100   407    0     0   1000      0 --:--:-- --:--:-- --:--:--  1000


### FASTQ 데이터 읽기

이제 `tfio.genome.read_fastq`를 사용하여 이 파일을 읽겠습니다(`tf.data` API는 곧 제공 예정).

In [5]:
fastq_data = tfio.genome.read_fastq(filename="test.fastq")
print(fastq_data.sequences)
print(fastq_data.raw_quality)

tf.Tensor(
[b'GATTACA'
 b'CGTTAGCGCAGGGGGCATCTTCACACTGGTGACAGGTAACCGCCGTAGTAAAGGTTCCGCCTTTCACT'
 b'CGGCTGGTCAGGCTGACATCGCCGCCGGCCTGCAGCGAGCCGCTGC' b'CGG'], shape=(4,), dtype=string)
tf.Tensor(
[b'BB>B@FA'
 b'AAAAABF@BBBDGGGG?FFGFGHBFBFBFABBBHGGGFHHCEFGGGGG?FGFFHEDG3EFGGGHEGHG'
 b'FAFAF;F/9;.:/;999B/9A.DFFF;-->.AAB/FC;9-@-=;=.' b'FAD'], shape=(4,), dtype=string)


보는 바와 같이 반환된 `fastq_data`에는 시퀀스에서 읽은 각 기본 정보의 품질에 관한 Phred 인코딩 품질 정보를 포함하는 `fastq_data.raw_quality`와 함께 fastq 파일(각각 크기가 다를 수 있음)에 있는 모든 시퀀스의 문자열 텐서인 `fastq_data.sequences`가 있습니다.

### 품질

관심이 있는 경우 도우미 op를 사용하여 이 품질 정보를 확률로 변환할 수 있습니다.

In [6]:
quality = tfio.genome.phred_sequences_to_probability(fastq_data.raw_quality)
print(quality.shape)
print(quality.row_lengths().numpy())
print(quality)

Instructions for updating:
Use fn_output_signature instead


(4, None, 1)
[ 7 68 46  3]
<tf.RaggedTensor [[[0.0005011872854083776], [0.0005011872854083776], [0.0012589250691235065], [0.0005011872854083776], [0.0007943279924802482], [0.00019952619913965464], [0.0006309573072940111]], [[0.0006309573072940111], [0.0006309573072940111], [0.0006309573072940111], [0.0006309573072940111], [0.0006309573072940111], [0.0005011872854083776], [0.00019952619913965464], [0.0007943279924802482], [0.0005011872854083776], [0.0005011872854083776], [0.0005011872854083776], [0.0003162277862429619], [0.0001584893325343728], [0.0001584893325343728], [0.0001584893325343728], [0.0001584893325343728], [0.0010000000474974513], [0.00019952619913965464], [0.00019952619913965464], [0.0001584893325343728], [0.00019952619913965464], [0.0001584893325343728], [0.00012589251855388284], [0.0005011872854083776], [0.00019952619913965464], [0.0005011872854083776], [0.00019952619913965464], [0.0005011872854083776], [0.00019952619913965464], [0.0006309573072940111], [0.000501187285408

### 원-핫 인코딩

또한, 원-핫 인코더를 사용하여 `A` `T` `C` `G` 염기 서열로 구성된 게놈 시퀀스 데이터를 인코딩할 수도 있습니다. 인코딩에 도움이 되는 내장 연산이 있습니다.


In [7]:
print(tfio.genome.sequences_to_onehot.__doc__)

Convert DNA sequences into a one hot nucleotide encoding.

    Each nucleotide in each sequence is mapped as follows:
    A -> [1, 0, 0, 0]
    C -> [0, 1, 0, 0]
    G -> [0 ,0 ,1, 0]
    T -> [0, 0, 0, 1]

    If for some reason a non (A, T, C, G) character exists in the string, it is
    currently mapped to a error one hot encoding [1, 1, 1, 1].

    Args:
        sequences: A tf.string tensor where each string represents a DNA sequence

    Returns:
        tf.RaggedTensor: The output sequences with nucleotides one hot encoded.
    


In [8]:
print(tfio.genome.sequences_to_onehot.__doc__)

Convert DNA sequences into a one hot nucleotide encoding.

    Each nucleotide in each sequence is mapped as follows:
    A -> [1, 0, 0, 0]
    C -> [0, 1, 0, 0]
    G -> [0 ,0 ,1, 0]
    T -> [0, 0, 0, 1]

    If for some reason a non (A, T, C, G) character exists in the string, it is
    currently mapped to a error one hot encoding [1, 1, 1, 1].

    Args:
        sequences: A tf.string tensor where each string represents a DNA sequence

    Returns:
        tf.RaggedTensor: The output sequences with nucleotides one hot encoded.
    
